In [37]:
### Install spaCy and download pipelines

!pip install spacy
import spacy

!spacy download fr_dep_news_trf
!spacy download fr_core_news_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 397.7/397.7 MB 49.7 MB/s eta 0:00:0000:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('fr_dep_news_trf')
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.3/16.3 MB 62.0 MB/s eta 0:00:0000:01
✔ Download and installation successful
You can now load the package via spacy.load('fr_core_news_sm')


In [38]:
# Read in and view data
import os
import pandas as pd
mg_df = pd.read_csv('mg_df.csv')
mg_df.head()

Bibliographies  \
0  Le Mercure galant, [janvier-avril] 1672 [tome ...   
1  Le Mercure galant, [janvier-avril] 1672 [tome ...   
2  Le Mercure galant, [janvier-avril] 1672 [tome ...   
3  Le Mercure galant, [janvier-avril] 1672 [tome ...   
4  Le Mercure galant, [janvier-avril] 1672 [tome ...   

                                              Titles  \
0                             Le Libraire au lecteur   
1                               Dessein de l’Ouvrage   
2                    L’Histoire du Collier de Perles   
3  Honneurs rendus à la mémoire de feüe Madame de...   
4               Éloge de Monsieur l’Abbé de Noailles   

                                            Articles  
0  Le Libraire Au Lecteur. CE Livre doit avoir de...  
1  MADAME, Il n’estoit pas besoin de me faire sou...  
2  c’est pourquoy je commence par une Histoire, a...  
3  Quoy que mon dessein ne soit pas de vous entre...  
4  Je ne sçais si je vous dois mander que Mr l’Ab...

In [39]:
# Find number of total 1-grams in entire corpus (body text).
#!pip install nltk
import nltk
from nltk import ngrams

unigram_sum = 0
for article in mg_df['Articles']:
    unigram_sum += len(list(ngrams(str(article).split(), 1)))

unigram_sum

5493293

In [40]:
## Define NLP process function for df.apply and df.parallel_apply

# def process_text(text):
#    return nlp(text)

In [41]:
# # Use Pandarallel to improve pipeline processing speed

# !pip install pandarallel

# from pandarallel import pandarallel as pl

# pl.initialize(progress_bar = True)

In [42]:
# # Process articles with dependency (larger) pipeline
# import fr_dep_news_trf
# from spacy.tokens import DocBin

# # Load dep model into NLP
# nlp = fr_dep_news_trf.load()

# # Process articles through pipeline -- can take roughly 100+ mins
# mg_df['Dep Docs'] = mg_df['Articles'].parallel_apply(process_text)

# # Create DocBin to serialize Docs so they can be loaded in later without re-running the pipeline
# doc_bin = DocBin(docs = mg_df['Dep Docs'])

# # Write DocBin object to disk for later use
# doc_bin.to_disk('./mg_fr_dep_news_trf.spacy')

In [43]:
# # Process articles with core (small) pipeline
# import fr_core_news_sm

# # Load core model into NLP
# nlp = fr_core_news_sm.load()

# # Process articles through pipeline -- takes roughly 2-4 mins
# mg_df['Core Docs'] = mg_df['Articles'].parallel_apply(process_text)

# # Create DocBin to serialize Docs so they can be loaded in later without re-running the pipeline
# docbin = DocBin(docs = mg_df['Core Docs'])

# # Write DocBin object to disk for later use
# docbin.to_disk('./mg_fr_core_docs.spacy')

In [44]:
# Load DocBin serialization and test that it contains the correct data
import fr_dep_news_trf
from spacy.tokens import DocBin

nlp = fr_dep_news_trf.load()
docbintakeout = DocBin().from_disk('./mg_fr_dep_news_trf.spacy')

docs_dep_news_trf = list(docbintakeout.get_docs(nlp.vocab))

testdoc = docs_dep_news_trf[0]
for token in testdoc:
    print(token.text, token.lemma_)

Le le
Libraire libraire
Au au
Lecteur lecteur
. .
CE ce
Livre livre
doit devoir
avoir avoir
dequoy dequoy
plaire plaire
à à
tout tout
le le
monde monde
, ,
à à
cause cause
de de
la le
diversité diversité
des de
matieres matiere
dont dont
il il
est être
remply remply
: :
Ceux celui
qui qui
aiment aimer
que que
les le
Romans roman
, ,
y y
trouveront trouver
des un
Histoires histoire
divertissantes divertissant
. .
Les le
Curieux curieux
des de
Nouvelles nouvelle
, ,
& et
les le
Provinciaux provincial
& et
les le
Etrangers etranger
, ,
qui qui
n’ n’
ont avoir
aucune aucun
connoissance connoissance
de de
plusieurs plusieurs
Personnes personne
d’ d’
une un
grande grand
naissance naissance
, ,
ou ou
d’ d’
un un
grand grand
mérite mérite
, ,
dont dont
ils il
entendent entendre
souvent souvent
parler parler
, ,
apprendront apprendre
dans dans
ce ce
Volume volume
& et
dans dans
les le
suivans suivan
, ,
par par
où où
ils il
sont être
recommandables recommandable
, ,
& et
ce ce
qui qui
les le
fa

In [45]:
# Add dep Doc objects to our dataframe
def get_tokens(doc):
    return [(token.text) for token in doc]
mg_df['Tokens'] = list(map(get_tokens, docs_dep_news_trf))
mg_df['Article Dep Docs'] = docs_dep_news_trf
mg_df.head()

Bibliographies  \
0  Le Mercure galant, [janvier-avril] 1672 [tome ...   
1  Le Mercure galant, [janvier-avril] 1672 [tome ...   
2  Le Mercure galant, [janvier-avril] 1672 [tome ...   
3  Le Mercure galant, [janvier-avril] 1672 [tome ...   
4  Le Mercure galant, [janvier-avril] 1672 [tome ...   

                                              Titles  \
0                             Le Libraire au lecteur   
1                               Dessein de l’Ouvrage   
2                    L’Histoire du Collier de Perles   
3  Honneurs rendus à la mémoire de feüe Madame de...   
4               Éloge de Monsieur l’Abbé de Noailles   

                                            Articles  \
0  Le Libraire Au Lecteur. CE Livre doit avoir de...   
1  MADAME, Il n’estoit pas besoin de me faire sou...   
2  c’est pourquoy je commence par une Histoire, a...   
3  Quoy que mon dessein ne soit pas de vous entre...   
4  Je ne sçais si je vous dois mander que Mr l’Ab...   

                                              Tokens  \
0  [Le, Libraire, Au, Lecteur, ., CE, Livre, doit...   
1  [MADAME, ,, Il, n’, estoit, pas, besoin, de, m...   
2  [c’, est, pourquoy, je, commence, par, une, Hi...   
3  [Quoy, que, mon, dessein, ne, soit, pas, de, v...   
4  [Je, ne, sçais, si, je, vous, dois, mander, qu...   

                                    Article Dep Docs  
0  (Le, Libraire, Au, Lecteur, ., CE, Livre, doit...  
1  (MADAME, ,, Il, n’, estoit, pas, besoin, de, m...  
2  (c’, est, pourquoy, je, commence, par, une, Hi...  
3  (Quoy, que, mon, dessein, ne, soit, pas, de, v...  
4  (Je, ne, sçais, si, je, vous, dois, mander, qu...

In [46]:
# Add core Doc objects to our dataframe
import fr_core_news_sm
nlp = fr_core_news_sm.load()
docbintakeout_core = DocBin().from_disk('./mg_fr_core_docs.spacy')
docs_core = list(docbintakeout_core.get_docs(nlp.vocab))
mg_df['Article Core Docs'] = docs_core

In [47]:
# Define functions for getting the tokens and lemmas of each document
def get_tokens(doc):
    return [(token.text) for token in doc]
def get_lemmas(doc):
    return [(token.lemma_) for token in doc]

# Generate dataframe to compare the lemmas of each pipeline
token_lemma = pd.concat(
    [
        mg_df['Article Core Docs'].apply(get_tokens).to_frame(),
        mg_df['Article Dep Docs'].apply(get_lemmas).to_frame(),
        mg_df['Article Core Docs'].apply(get_lemmas).to_frame()
    ],
    axis = 1,
)
token_lemma.columns = ['tokens', 'dep_lemmas', 'core_lemmas']


In [48]:
# Gather instances where the lemmas were not the same
all_lemma_diffs = []
for doc in token_lemma.itertuples():
    doc_diffs = []
    for token, dep_lem, core_lem in zip(doc.tokens, doc.dep_lemmas, doc.core_lemmas):
        if dep_lem != core_lem:
            doc_diffs.append([token, dep_lem, core_lem])
    all_lemma_diffs.append(doc_diffs)
all_lemma_diffs

[[['Lecteur', 'lecteur', 'Lecteur'],
  ['Romans', 'roman', 'Romans'],
  ['des', 'un', 'de'],
  ['Nouvelles', 'nouvelle', 'Nouvelles'],
  ['Galant', 'galant', 'Galant'],
  ['Etrangères', 'etrangère', 'Etrangères'],
  ['L’', 'l’', 'L’'],
  ['Monde', 'monde', 'Monde'],
  ['Essays', 'essay', 'Essays'],
  ['achevé', 'achever', 'achevé'],
  ['obligé', 'obliger', 'obligé'],
  ['des', 'de', 'un'],
  ['parle', 'parler', 'parle'],
  ['necessaire', 'necessair', 'necessaire'],
  ['écrire', 'écrire', 'écrir'],
  ['des', 'un', 'de'],
  ['Galanteries', 'galanterie', 'Galanteries']],
 [['nouvelles', 'nouvelle', 'nouveau'],
  ['facilement', 'facilement', 'facilemer'],
  ['Passons', 'passer', 'passon'],
  ['nouvelles', 'nouvelle', 'nouveau'],
  ['des', 'de', 'un'],
  ['Gazettes', 'gazette', 'Gazettes'],
  ['Mariages', 'mariage', 'Mariages'],
  ['nouvelles', 'nouvelle', 'nouveau'],
  ['mesmes', 'mesmes', 'mesme'],
  ['toûjours', 'toûjours', 'toûjour'],
  ['instruite', 'instruire', 'instruite'],
  ['fait'

In [49]:
# Start analyzing instances in which lemmas were not the same
compare_lemma_df = pd.DataFrame({'lemmas': all_lemma_diffs})
compare_lemma_df['diff_count'] = compare_lemma_df['lemmas'].apply(len)
compare_lemma_df

lemmas  diff_count
0     [[Lecteur, lecteur, Lecteur], [Romans, roman, ...          17
1     [[nouvelles, nouvelle, nouveau], [facilement, ...          38
2     [[nouvelles, nouvelle, nouveau], [parloient, p...          82
3     [[toûjours, toûjours, toûjour], [nouvelles, no...          10
4     [[Abbé, abbé, Abbé], [dernierement, derniereme...          15
...                                                 ...         ...
8027  [[Apprenez, apprendre, apprenez], [Amour, amou...           2
8028  [[Air, air, Air], [Oiseau, oiseau, Oiseau], [o...          11
8029  [[CHANSON, CHANSON, chanson], [cesse, cesse, c...           5
8030  [[CHANSON, CHANSON, chanson], [L’, l’, L’], [A...           6
8031  [[Menuet/, Menuet/, menuet/], [Menuet, menuet,...          11

[8032 rows x 2 columns]

In [50]:
# Summary of the counts of lemma differences per article
compare_lemma_df['diff_count'].describe()

count    8032.000000
mean       59.861429
std       102.392950
min         0.000000
25%        13.000000
50%        29.000000
75%        69.000000
max      2367.000000
Name: diff_count, dtype: float64

In [51]:
# One article had 2367 differences in lemmas! Let's explore which one
max_offender = compare_lemma_df.loc[compare_lemma_df.diff_count==2367, 'lemmas']
print(max_offender.index[0])
print(max_offender.values[0])

6372
[['temps', 'temp', 'temps'], ['Messeigneurs', 'monseigneur', 'Messeigneurs'], ['Bourg', 'bourg', 'Bourg'], ['appellé', 'appeller', 'appellé'], ['belle', 'bel', 'beau'], ['Sainfons', 'Sainfons', 'sainfon'], ['aprés', 'aprés', 'aprer'], ['vêtuës', 'vêtuës', 'vêtuë'], ['des', 'un', 'de'], ['Marquis', 'marquis', 'Marquis'], ['Messeigneurs', 'monseigneur', 'Messeigneurs'], ['Faubourg', 'faubourg', 'Faubourg'], ['Aprés', 'aprés', 'aprer'], ['Academistes', 'academiste', 'Academistes'], ['formerent', 'formerer', 'formerent'], ['des', 'de', 'un'], ['Pavant', 'Pavant', 'pavant'], ['Ecuyer', 'ecuyer', 'Ecuyer'], ['Academie', 'academie', 'Academie'], ['épée', 'épée', 'éper'], ['Mr', 'mr', 'Mr'], ['Criminel', 'Criminel', 'criminel'], ['Robe', 'robe', 'Robe'], ['Archers', 'archer', 'Archers'], ['Compagnie', 'compagnie', 'Compagnie'], ['Fauxbourg', 'fauxbourg', 'Fauxbourg'], ['Aprés', 'aprés', 'aprer'], ['Cavalerie', 'cavalerie', 'Cavalerie'], ['trouverent', 'trouverer', 'trouverent'], ['estoien

In [52]:
# The worst offender was this article!
mg_df.iloc[6372]

Bibliographies       Mercure galant, mai 1701 [deuxième partie] [to...
Titles               Suite du Voyage de Messeigneurs les Princes. C...
Articles             Il est temps que je finisse ce Journal que j’a...
Tokens               [Il, est, temps, que, je, finisse, ce, Journal...
Article Dep Docs     (Il, est, temps, que, je, finisse, ce, Journal...
Article Core Docs    (Il, est, temps, que, je, finisse, ce, Journal...
Name: 6372, dtype: object

In [53]:
# Now, let's create a similar dataframe but include parts-of-speech (POS)
def get_tokens(doc):
    return [(token.text) for token in doc]
def get_lemmas(doc):
    return [(token.lemma_) for token in doc]
def get_pos(doc):
    return [(token.pos_) for token in doc]

token_lemmas_pos = pd.concat(
    [
        mg_df['Article Core Docs'].apply(get_tokens).to_frame(),
        mg_df['Article Dep Docs'].apply(get_lemmas).to_frame(),
        mg_df['Article Core Docs'].apply(get_lemmas).to_frame(),
        mg_df['Article Dep Docs'].apply(get_pos).to_frame(),
        mg_df['Article Core Docs'].apply(get_pos).to_frame()
    ],
    axis = 1,
)
token_lemmas_pos.columns = ['tokens', 'dep_lemmas', 'core_lemmas', 'dep_pos', 'core_pos']
token_lemmas_pos

tokens  \
0     [Le, Libraire, Au, Lecteur, ., CE, Livre, doit...   
1     [MADAME, ,, Il, n’, estoit, pas, besoin, de, m...   
2     [c’, est, pourquoy, je, commence, par, une, Hi...   
3     [Quoy, que, mon, dessein, ne, soit, pas, de, v...   
4     [Je, ne, sçais, si, je, vous, dois, mander, qu...   
...                                                 ...   
8027  [CHANSON, ., Je, vous, nomme, sans, que, j', y...   
8028  [Nous, ne, donnons, la, Pastorale, suivante, q...   
8029  [CHANSON, ., L', air, est, de, Monsieur, Moure...   
8030  [CHANSON, ., L’, Air, est, de, M., Mourette, ....   
8031  [CHANSON, Au, départ, de, la, musique, :, «, M...   

                                             dep_lemmas  \
0     [le, libraire, au, lecteur, ., ce, livre, devo...   
1     [monsieur, ,, il, n’, estoit, pas, besoin, de,...   
2     [c’, être, pourquoy, je, commencer, par, un, h...   
3     [quoy, que, mon, dessein, ne, être, pas, de, v...   
4     [je, ne, sçer, si, je, vous, devoir, mander, q...   
...                                                 ...   
8027  [chanson, ., je, vous, nommer, sans, que, je, ...   
8028  [nous, ne, donner, le, pastorale, suivant, qu’...   
8029  [CHANSON, ., le, air, être, de, Monsieur, Mour...   
8030  [CHANSON, ., l’, air, être, de, m., Mourette, ...   
8031  [chanson, au, départ, de, le, musique, :, «, m...   

                                            core_lemmas  \
0     [le, libraire, au, Lecteur, ., ce, livre, devo...   
1     [monsieur, ,, il, n’, estoit, pas, besoin, de,...   
2     [c’, être, pourquoy, je, commencer, par, un, h...   
3     [quoy, que, mon, dessein, ne, être, pas, de, v...   
4     [je, ne, sçer, si, je, vous, devoir, mander, q...   
...                                                 ...   
8027  [chanson, ., je, vous, nommer, sans, que, je, ...   
8028  [nous, ne, donner, le, pastorale, suivant, qu’...   
8029  [chanson, ., le, air, être, de, Monsieur, Mour...   
8030  [chanson, ., L’, Air, être, de, m., Mourette, ...   
8031  [chanson, au, départ, de, le, musique, :, «, m...   

                                                dep_pos  \
0     [DET, NOUN, ADP, NOUN, PUNCT, DET, NOUN, VERB,...   
1     [NOUN, PUNCT, PRON, ADV, VERB, ADV, NOUN, ADP,...   
2     [PRON, AUX, ADV, PRON, VERB, ADP, DET, NOUN, P...   
3     [ADV, SCONJ, DET, NOUN, ADV, VERB, ADV, ADP, P...   
4     [PRON, ADV, VERB, SCONJ, PRON, PRON, VERB, VER...   
...                                                 ...   
8027  [NOUN, PUNCT, PRON, PRON, VERB, ADP, SCONJ, PR...   
8028  [PRON, ADV, VERB, DET, NOUN, ADJ, ADV, ADP, NO...   
8029  [PROPN, PUNCT, DET, NOUN, AUX, ADP, NOUN, PROP...   
8030  [PROPN, PUNCT, DET, NOUN, AUX, ADP, NOUN, PROP...   
8031  [NOUN, ADP, NOUN, ADP, DET, NOUN, PUNCT, PUNCT...   

                                               core_pos  
0     [DET, NOUN, ADP, PROPN, PUNCT, DET, NOUN, VERB...  
1     [NOUN, PUNCT, PRON, PROPN, VERB, ADV, NOUN, AD...  
2     [ADJ, AUX, ADV, PRON, VERB, ADP, DET, NOUN, PU...  
3     [ADJ, SCONJ, DET, NOUN, ADV, AUX, ADV, ADP, PR...  
4     [PRON, ADV, VERB, SCONJ, PRON, PRON, VERB, VER...  
...                                                 ...  
8027  [NOUN, PUNCT, PRON, PRON, VERB, ADP, SCONJ, PR...  
8028  [PRON, ADV, VERB, DET, NOUN, ADJ, NOUN, ADP, N...  
8029  [NOUN, PUNCT, DET, NOUN, AUX, ADP, NOUN, PROPN...  
8030  [NOUN, PUNCT, PROPN, PROPN, AUX, ADP, NOUN, PR...  
8031  [NOUN, ADP, NOUN, ADP, DET, NOUN, PUNCT, PROPN...  

[8032 rows x 5 columns]

In [54]:
# Find occurences where the lemmas were different between pipelines AND the part of speech was different
all_lemma_diffs_pos = []
for doc in token_lemmas_pos.itertuples():
    doc_diffs = []
    for token, dep_lem, core_lem, dep_pos, core_pos in zip(doc.tokens, doc.dep_lemmas, doc.core_lemmas, doc.dep_pos, doc.core_pos):
        if dep_lem != core_lem and dep_pos != core_pos:
            doc_diffs.append([token, dep_lem, dep_pos, core_lem, core_pos])
    all_lemma_diffs_pos.append(doc_diffs)
all_lemma_diffs_pos

[[['Lecteur', 'lecteur', 'NOUN', 'Lecteur', 'PROPN'],
  ['Romans', 'roman', 'NOUN', 'Romans', 'PROPN'],
  ['des', 'un', 'DET', 'de', 'ADP'],
  ['Nouvelles', 'nouvelle', 'NOUN', 'Nouvelles', 'PROPN'],
  ['Galant', 'galant', 'ADJ', 'Galant', 'PROPN'],
  ['Etrangères', 'etrangère', 'ADJ', 'Etrangères', 'PROPN'],
  ['L’', 'l’', 'DET', 'L’', 'PROPN'],
  ['Monde', 'monde', 'NOUN', 'Monde', 'PROPN'],
  ['Essays', 'essay', 'NOUN', 'Essays', 'PROPN'],
  ['achevé', 'achever', 'VERB', 'achevé', 'ADJ'],
  ['obligé', 'obliger', 'VERB', 'obligé', 'NOUN'],
  ['des', 'de', 'ADP', 'un', 'DET'],
  ['parle', 'parler', 'VERB', 'parle', 'NOUN'],
  ['necessaire', 'necessair', 'ADJ', 'necessaire', 'NOUN'],
  ['écrire', 'écrire', 'VERB', 'écrir', 'ADJ'],
  ['des', 'un', 'DET', 'de', 'ADP'],
  ['Galanteries', 'galanterie', 'NOUN', 'Galanteries', 'PROPN']],
 [['nouvelles', 'nouvelle', 'NOUN', 'nouveau', 'ADJ'],
  ['facilement', 'facilement', 'ADV', 'facilemer', 'VERB'],
  ['Passons', 'passer', 'VERB', 'passon',

In [55]:
# Create dataframe to count the length of 'differences'
compare_lemma_pos_df = pd.DataFrame({'lemmas': all_lemma_diffs_pos})
compare_lemma_pos_df['diff_count'] = compare_lemma_pos_df['lemmas'].apply(len)
compare_lemma_pos_df

lemmas  diff_count
0     [[Lecteur, lecteur, NOUN, Lecteur, PROPN], [Ro...          17
1     [[nouvelles, nouvelle, NOUN, nouveau, ADJ], [f...          38
2     [[nouvelles, nouvelle, NOUN, nouveau, ADJ], [p...          82
3     [[toûjours, toûjours, ADV, toûjour, ADJ], [nou...          10
4     [[Abbé, abbé, NOUN, Abbé, PROPN], [dernieremen...          15
...                                                 ...         ...
8027  [[Apprenez, apprendre, VERB, apprenez, NOUN], ...           2
8028  [[Air, air, NOUN, Air, PROPN], [Oiseau, oiseau...          11
8029  [[CHANSON, CHANSON, PROPN, chanson, NOUN], [ce...           5
8030  [[CHANSON, CHANSON, PROPN, chanson, NOUN], [L’...           6
8031  [[Menuet/, Menuet/, PROPN, menuet/, VERB], [Me...          11

[8032 rows x 2 columns]

In [56]:
# Print the first comparison (lemma differs) to the seocnd comparison (lemma AND POS differs)
# Note that these descriptions are EXACTLY the same-- whenever the lemma differs, the part of speech also differs
print(compare_lemma_df.describe(), "\n", compare_lemma_pos_df.describe())

        diff_count
count  8032.000000
mean     59.861429
std     102.392950
min       0.000000
25%      13.000000
50%      29.000000
75%      69.000000
max    2367.000000 
         diff_count
count  8032.000000
mean     59.861429
std     102.392950
min       0.000000
25%      13.000000
50%      29.000000
75%      69.000000
max    2367.000000


In [57]:
# Knowing that either or both of the models suffers from differences between its training text and this text, let's try to modify
# our corpus' orthography to improve the performances of both.
import re
from collections import Counter

y_to_i = []
for doc in token_lemma['tokens']:
    for token in doc:
        if re.search(r'y', token):
            y_to_i.append(token.lower())

# Finds the most common tokens that have 'y' anywhere in them
counts = Counter(y_to_i)
counts.most_common(100)

[('luy', 29407),
 ('y', 25618),
 ('roy', 12009),
 ('ay', 5981),
 ('ayant', 5822),
 ('quoy', 4835),
 ('celuy', 4372),
 ('ny', 3521),
 ('yeux', 3180),
 ('moy', 3094),
 ('joye', 2804),
 ('icy', 2367),
 ('voicy', 1860),
 ('huy', 1680),
 ('envoye', 1546),
 ('vray', 1458),
 ('voyoit', 1407),
 ('parmy', 1319),
 ('royale', 1281),
 ('cy', 1131),
 ('foy', 1121),
 ('toy', 1073),
 ('reyne', 1028),
 ('sçay', 1011),
 ('royaume', 958),
 ('moyen', 912),
 ('amy', 863),
 ('mary', 859),
 ('croy', 853),
 ('pourquoy', 833),
 ('voyant', 820),
 ('party', 792),
 ('envoyé', 770),
 ('pays', 694),
 ('envoyer', 638),
 ('voyage', 610),
 ('voyez', 569),
 ('suivy', 559),
 ('loy', 550),
 ('croyoit', 532),
 ('remply', 520),
 ('demy', 510),
 ('royal', 504),
 ('roys', 494),
 ('envoya', 493),
 ('midy', 464),
 ('dequoy', 449),
 ('ayent', 449),
 ('diray', 444),
 ('employ', 441),
 ('lyon', 440),
 ('abbaye', 436),
 ('lys', 421),
 ('servy', 389),
 ('soy', 387),
 ('voy', 384),
 ('savoye', 364),
 ('moyens', 357),
 ('hyver', 337

In [58]:
# Using the 100 most common occurences of 'y', I made my best attempt at generating a list of words in which 'y' SHOULD be included,
# and should not be changed to 'i'. Note some strange tokens at the end, like jy and sy. In order to create substitutions for the pipeline,
# I must do it with the un-tokenized, original text, after removing capitalization and punctuation. Therefore, J'y gets recognized as correct
# because it matches jy. However, ny should NOT be in this list, because the token ny needs to be changed to ni, but n'y should remain.
import string
y_stops = ("ayant, envoye, y, voyait, royaume, moyen, voyant, envoyé, pays, envoyer, voyage, " +
        "voyez, royal, royale, envoya, lyon, abbaye, moyens, savoye, voyons, berry, rayons, hymen, " +
        "employer, soyez, croyez, croyoit, croyait, envoyez, envy, ecuyer, croy, "+
        "essayer, symphonie, payé, paya, payer, croyant, jy, sy, dy, ly, employe, yeux").split(", ")

# Define a function to replace all archaic y characters
def replace_y(str, stops):
    cleaned = []
    words = str.split(" ")
    for word in words:
        # Boolean to see if word is contained within stop list -- punctuation is removed and word is lowercased EXCEPT n'y because ny -> ni is correct
        exceptions = word.translate(str.maketrans('','', string.punctuation)).lower() in stops or word in ["n’y", "n'y"]
        # Replace y with i if not an exception and add either the unmodified or modified word to the cleaned list.
        if 'y' in word and not(exceptions):
            word = word.replace('y', 'i')
            cleaned.append(word)
        else:
            cleaned.append(word)
    # Join all the replaced words back into one string
    return " ".join(cleaned)
# Define new dataframe
cleaned_mg_df = pd.DataFrame()

# Define original text in new dataframe
cleaned_mg_df['original'] = mg_df['Articles']

# Apply our new function to the original text
cleaned_mg_df['no_y'] = mg_df['Articles'].apply(lambda x: replace_y(x, y_stops))
cleaned_mg_df

original  \
0     Le Libraire Au Lecteur. CE Livre doit avoir de...   
1     MADAME, Il n’estoit pas besoin de me faire sou...   
2     c’est pourquoy je commence par une Histoire, a...   
3     Quoy que mon dessein ne soit pas de vous entre...   
4     Je ne sçais si je vous dois mander que Mr l’Ab...   
...                                                 ...   
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...   
8028  Nous ne donnons la Pastorale suivante qu’en fa...   
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...   
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...   
8031  CHANSON Au départ de la musique : « May 1721/ ...   

                                                   no_y  
0     Le Libraire Au Lecteur. CE Livre doit avoir de...  
1     MADAME, Il n’estoit pas besoin de me faire sou...  
2     c’est pourquoi je commence par une Histoire, a...  
3     Quoi que mon dessein ne soit pas de vous entre...  
4     Je ne sçais si je vous dois mander que Mr l’Ab...  
...                                                 ...  
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...  
8028  Nous ne donnons la Pastorale suivante qu’en fa...  
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...  
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...  
8031  CHANSON Au départ de la musique : « Mai 1721/ ...  

[8032 rows x 2 columns]

In [59]:
for x, y in cleaned_mg_df['original'].items():
    if type(y) == float:
        print(x, y)
        break

In [60]:
# Perform the same orthographic analysis on -oit, -ois, and -oient words
import re
from collections import Counter

o_conj = []
for doc in token_lemma['tokens']:
    for token in doc:
        if re.search(r'oit', token) or re.search(r'ois$', token) or re.search(r'oient', token):
            o_conj.append(token.lower())

counts = Counter(o_conj)
counts.most_common(100)

[('avoit', 21841),
 ('estoit', 19567),
 ('estoient', 6615),
 ('trois', 4683),
 ('avoient', 4432),
 ('doit', 4190),
 ('soit', 3682),
 ('mois', 3595),
 ('fois', 3301),
 ('voit', 2912),
 ('pouvoit', 2761),
 ('faisoit', 2722),
 ('auroit', 2397),
 ('seroit', 2365),
 ('devoit', 1949),
 ('françois', 1772),
 ('étoit', 1479),
 ('voyoit', 1407),
 ('vouloit', 1239),
 ('rois', 1172),
 ('faisoient', 1110),
 ('quelquefois', 1076),
 ('pourroit', 1006),
 ('droit', 926),
 ('bois', 896),
 ('autrefois', 845),
 ('venoit', 825),
 ('soient', 813),
 ('endroits', 793),
 ('falloit', 775),
 ('étoient', 763),
 ('donnoit', 729),
 ('endroit', 712),
 ('avois', 684),
 ('droite', 680),
 ('sçauroit', 659),
 ('exploits', 632),
 ('disoit', 625),
 ('croit', 610),
 ('hautbois', 610),
 ('sçavoit', 605),
 ('alloit', 593),
 ('dois', 592),
 ('feroit', 574),
 ('vois', 574),
 ('pouvoient', 566),
 ('auroient', 564),
 ('trouvoit', 558),
 ('devoient', 557),
 ('paroissoit', 552),
 ('croyoit', 532),
 ('aimoit', 504),
 ('seroient', 4

In [61]:
# Generate stop words, replace archaic orthography with o -> a shift
o_stops = ("trois, doit, soit, mois, devoit, rois, quelquefois, fois, " + 
        "droit, bois, autrefois, endroits, endroit, droite, exploits, " +
        "croit, dois, vois, bourgeois, droits, crois, moitié, reçoit, emplois").split(', ')

def replace_o(str, stops):
    cleaned = []
    words = str.split(" ")
    for word in words:
        if 'oit' in word and not(word.translate(str.maketrans('','', string.punctuation)).lower() in stops):
            word = word.replace('oit', 'ait')
            cleaned.append(word)
        elif re.search(r'ois$', word) and not(word.translate(str.maketrans('','', string.punctuation)).lower() in stops):
            word = word.replace('ois', 'ais')
            cleaned.append(word)
        elif 'oient' in word and not(word.translate(str.maketrans('','', string.punctuation)).lower() in stops):
            word = word.replace('oient', 'aient')
            cleaned.append(word)
        else:
            cleaned.append(word)
    return " ".join(cleaned)
# Apply o->a replacement to no_y text
cleaned_mg_df['no_o'] = cleaned_mg_df['no_y'].apply(lambda x: replace_o(x, o_stops))
cleaned_mg_df

original  \
0     Le Libraire Au Lecteur. CE Livre doit avoir de...   
1     MADAME, Il n’estoit pas besoin de me faire sou...   
2     c’est pourquoy je commence par une Histoire, a...   
3     Quoy que mon dessein ne soit pas de vous entre...   
4     Je ne sçais si je vous dois mander que Mr l’Ab...   
...                                                 ...   
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...   
8028  Nous ne donnons la Pastorale suivante qu’en fa...   
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...   
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...   
8031  CHANSON Au départ de la musique : « May 1721/ ...   

                                                   no_y  \
0     Le Libraire Au Lecteur. CE Livre doit avoir de...   
1     MADAME, Il n’estoit pas besoin de me faire sou...   
2     c’est pourquoi je commence par une Histoire, a...   
3     Quoi que mon dessein ne soit pas de vous entre...   
4     Je ne sçais si je vous dois mander que Mr l’Ab...   
...                                                 ...   
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...   
8028  Nous ne donnons la Pastorale suivante qu’en fa...   
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...   
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...   
8031  CHANSON Au départ de la musique : « Mai 1721/ ...   

                                                   no_o  
0     Le Libraire Au Lecteur. CE Livre doit avoir de...  
1     MADAME, Il n’estait pas besoin de me faire sou...  
2     c’est pourquoi je commence par une Histoire, a...  
3     Quoi que mon dessein ne soit pas de vous entre...  
4     Je ne sçais si je vous dois mander que Mr l’Ab...  
...                                                 ...  
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...  
8028  Nous ne donnons la Pastorale suivante qu’en fa...  
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...  
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...  
8031  CHANSON Au départ de la musique : « Mai 1721/ ...  

[8032 rows x 3 columns]

In [63]:
# Apply orthographic changes to remove archaic ç
import re
from collections import Counter

cedille = []
for doc in token_lemma['tokens']:
    for token in doc:
        if re.search(r'sç', token):
            cedille.append(token.lower())

counts = Counter(cedille)
counts.most_common(100)

[('sçavoir', 1722),
 ('sçait', 1291),
 ('sçay', 1011),
 ('sçavez', 772),
 ('sçauroit', 657),
 ('sçavoit', 601),
 ('sçavant', 313),
 ('sçeu', 285),
 ('sçavent', 262),
 ('sçais', 207),
 ('sçavans', 178),
 ('sçaurois', 170),
 ('sçavante', 170),
 ('sçachant', 159),
 ('sçeut', 137),
 ('sçauroient', 137),
 ('sçache', 135),
 ('sçavantes', 119),
 ('sçaurez', 106),
 ('sçavoient', 99),
 ('sçaura', 96),
 ('sçû', 93),
 ('sçauriez', 81),
 ('sçavons', 60),
 ('sçavois', 56),
 ('sçu', 47),
 ('sçut', 31),
 ('sçaurions', 30),
 ('sçachiez', 30),
 ('sçût', 29),
 ('sçeust', 28),
 ('sçauront', 27),
 ('sçauray', 22),
 ('sçachez', 20),
 ('sçaviez', 20),
 ('sçeuë', 15),
 ('sçachent', 15),
 ('sçeuës', 13),
 ('sçeurent', 12),
 ('sçaurons', 12),
 ('sçavamment', 11),
 ('sçauras', 11),
 ('sçai', 10),
 ('sçavions', 9),
 ('sçachions', 7),
 ('sçuë', 6),
 ('sçus', 6),
 ('sçeussent', 5),
 ('sçeus', 5),
 ('sçavants', 5),
 ('sçience', 5),
 ('sçaurai', 3),
 ('sçeussiez', 3),
 ('insçeu', 3),
 ('sçust', 3),
 ('sçachans', 2),

In [64]:
# No stop words-- all instances of sç observed in the 100 most common words have been replaced with just s
cedille_stops = ("").split(', ')

def replace_o(str, stops):
    return re.sub(r'sç', 's', str)
cleaned_mg_df['no_cedille'] = cleaned_mg_df['no_o'].apply(lambda x: replace_o(x, cedille_stops))
cleaned_mg_df # Df progresses through transformations-- no_cedille includes them all

original  \
0     Le Libraire Au Lecteur. CE Livre doit avoir de...   
1     MADAME, Il n’estoit pas besoin de me faire sou...   
2     c’est pourquoy je commence par une Histoire, a...   
3     Quoy que mon dessein ne soit pas de vous entre...   
4     Je ne sçais si je vous dois mander que Mr l’Ab...   
...                                                 ...   
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...   
8028  Nous ne donnons la Pastorale suivante qu’en fa...   
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...   
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...   
8031  CHANSON Au départ de la musique : « May 1721/ ...   

                                                   no_y  \
0     Le Libraire Au Lecteur. CE Livre doit avoir de...   
1     MADAME, Il n’estoit pas besoin de me faire sou...   
2     c’est pourquoi je commence par une Histoire, a...   
3     Quoi que mon dessein ne soit pas de vous entre...   
4     Je ne sçais si je vous dois mander que Mr l’Ab...   
...                                                 ...   
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...   
8028  Nous ne donnons la Pastorale suivante qu’en fa...   
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...   
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...   
8031  CHANSON Au départ de la musique : « Mai 1721/ ...   

                                                   no_o  \
0     Le Libraire Au Lecteur. CE Livre doit avoir de...   
1     MADAME, Il n’estait pas besoin de me faire sou...   
2     c’est pourquoi je commence par une Histoire, a...   
3     Quoi que mon dessein ne soit pas de vous entre...   
4     Je ne sçais si je vous dois mander que Mr l’Ab...   
...                                                 ...   
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...   
8028  Nous ne donnons la Pastorale suivante qu’en fa...   
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...   
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...   
8031  CHANSON Au départ de la musique : « Mai 1721/ ...   

                                             no_cedille  
0     Le Libraire Au Lecteur. CE Livre doit avoir de...  
1     MADAME, Il n’estait pas besoin de me faire sou...  
2     c’est pourquoi je commence par une Histoire, a...  
3     Quoi que mon dessein ne soit pas de vous entre...  
4     Je ne sais si je vous dois mander que Mr l’Abb...  
...                                                 ...  
8027  CHANSON. Je vous nomme sans que j'y pense ; Vo...  
8028  Nous ne donnons la Pastorale suivante qu’en fa...  
8029  CHANSON. L'air est de Monsieur Mourette. À Ren...  
8030  CHANSON. L’Air est de M. Mourette. Ce fut dans...  
8031  CHANSON Au départ de la musique : « Mai 1721/ ...  

[8032 rows x 4 columns]

In [65]:
# Check the list of the 100 most common substitutions I've made to minimize mistaken subsitututions
# I caught yeux being changed to ieux before adding it to the stop list
subs = []
for doc in cleaned_mg_df.itertuples():
    if doc.original != doc.no_cedille:
        for x, y in zip(doc.original.split(" "), doc.no_cedille.split(" ")):
            if x != y:
                subs.append([x, y])
sub_list = Counter([x[0] for x in subs])
sub_list.most_common(100)

[('luy', 25297),
 ('avoit', 18172),
 ('estoit', 14579),
 ('Roy', 7414),
 ('estoient', 5560),
 ('celuy', 3657),
 ('avoient', 3543),
 ('Roy,', 3390),
 ('quoy', 3324),
 ('ny', 3274),
 ('voit', 2666),
 ('pouvoit', 2646),
 ('faisoit', 2539),
 ('seroit', 2242),
 ('j’ay', 2125),
 ('joye', 1906),
 ('s’y', 1856),
 ('n’avoit', 1772),
 ('auroit', 1659),
 ('luy,', 1614),
 ('ay', 1596),
 ('icy', 1562),
 ('moy', 1372),
 ('voyoit', 1333),
 ('sçavoir', 1332),
 ('n’estoit', 1313),
 ('sçait', 1213),
 ('Voicy', 1185),
 ('Quoy', 1173),
 ('Roy.', 1173),
 ('vouloit', 1170),
 ('l’avoit', 1158),
 ('parmy', 1121),
 ('s’estoit', 1100),
 ('faisoient', 1069),
 ('aujourd’huy', 1049),
 ('vray', 1032),
 ('François', 1018),
 ('étoit', 996),
 ('pourroit', 901),
 ('c’estoit', 889),
 ('sçay', 857),
 ('luy.', 840),
 ('moy,', 827),
 ('d’y', 816),
 ('J’ay', 794),
 ('venoit', 787),
 ('soient', 759),
 ('falloit', 725),
 ('donnoit', 663),
 ('Reyne', 641),
 ('sçauroit', 641),
 ('étoient', 630),
 ('n’ay', 623),
 ('voicy', 586),

In [66]:
#### This next set of code blocks applies the NLP pipelines to our modified text and serializes them so all our Doc objects
#### can be quickly loaded in from the disk for analysis.

In [67]:
# Workaround for multithreading issues
# import torch
# torch.set_num_threads(1) 

In [68]:
# import fr_core_news_sm
# nlp = fr_core_news_sm.load()

# pl.initialize(progress_bar = True, nb_workers = 5)


# cleaned_mg_df['Core Docs'] = cleaned_mg_df['no_cedille'].parallel_apply(process_text)


In [69]:
# doc_bin = DocBin()
# for doc in cleaned_mg_df['Core Docs']:
#     doc_bin.add(doc)

# doc_bin.to_disk('./clean_mg_core_docs.spacy')

In [70]:
# import fr_dep_news_trf
# nlp = fr_dep_news_trf.load()

# pl.initialize(progress_bar=True, nb_workers = 80)

# cleaned_mg_df['Dep Docs'] = cleaned_mg_df['no_cedille'].parallel_apply(process_text)

In [ ]:
# doc_bin = DocBin()
# for doc in cleaned_mg_df['Dep Docs']:
#     doc_bin.add(doc)

# doc_bin.to_disk('./clean_mg_dep_docs.spacy')

: 